# Working with parquet files

## Objective

+ In this assignment, we will use the data downloaded with the module `data_manager` to create features.

(11 pts total)

## Prerequisites

+ This notebook assumes that price data is available to you in the environment variable `PRICE_DATA`. If you have not done so, then execute the notebook `01_materials/labs/2_data_engineering.ipynb` to create this data set.


+ Load the environment variables using dotenv. (1 pt)

In [12]:
# Write your code below.

# Load env variable
from dotenv import load_dotenv
import os
import sys
import pandas as pd
import warnings
warnings.filterwarnings("ignore")

dotenv_path = '../../05_src/.env' #.env exists here
load_dotenv(dotenv_path=dotenv_path)


True

In [13]:
# Get Dask
import dask.dataframe as dd

In [14]:
import sys
sys.path.append("../../05_src") # logger exists here

In [15]:
# Get logger

from logger import get_logger
_logs = get_logger(__name__)
# _logs.info("Hello world!") # test to see if logger working

+ Load the environment variable `PRICE_DATA`.
+ Use [glob](https://docs.python.org/3/library/glob.html) to find the path of all parquet files in the directory `PRICE_DATA`.

(1pt)

In [16]:
import os
from glob import glob  # Import glob directly

# Configure logging
import logging
logging.basicConfig(level=logging.INFO)
_logs = logging.getLogger(__name__)

# Get path to PRICE_DATA
PRICE_DATA = os.getenv('PRICE_DATA') 
if PRICE_DATA is None: # Checks PRICE_DATA exists or not
    _logs.error("PRICE_DATA environment variable is not set.")
else:
    _logs.info("PRICE_DATA folder is in: %s", PRICE_DATA)

    # Use glob to find all parquet files
    parquet_files = glob(os.path.join(PRICE_DATA, "**/*.parquet"), recursive=True)  # Use glob directly
    _logs.info("Total parquet files is: %d", len(parquet_files))

    # Log the paths of the parquet files (optional)
    for file in parquet_files:
        _logs.info("Found parquet file: %s", file)



2024-10-27 19:24:26,790, 1622047410.py, 14, INFO, PRICE_DATA folder is in: ../../05_src/data/prices/
2024-10-27 19:24:26,790, 1622047410.py, 14, INFO, PRICE_DATA folder is in: ../../05_src/data/prices/
INFO:__main__:PRICE_DATA folder is in: ../../05_src/data/prices/
2024-10-27 19:24:27,985, 1622047410.py, 18, INFO, Total parquet files is: 22414
2024-10-27 19:24:27,985, 1622047410.py, 18, INFO, Total parquet files is: 22414
INFO:__main__:Total parquet files is: 22414
2024-10-27 19:24:28,000, 1622047410.py, 22, INFO, Found parquet file: ../../05_src/data/prices\A\A_2000.parquet
2024-10-27 19:24:28,000, 1622047410.py, 22, INFO, Found parquet file: ../../05_src/data/prices\A\A_2000.parquet
INFO:__main__:Found parquet file: ../../05_src/data/prices\A\A_2000.parquet
2024-10-27 19:24:28,003, 1622047410.py, 22, INFO, Found parquet file: ../../05_src/data/prices\A\A_2001.parquet
2024-10-27 19:24:28,003, 1622047410.py, 22, INFO, Found parquet file: ../../05_src/data/prices\A\A_2001.parquet
INFO:

For each ticker and using Dask, do the following:

+ Add lags for variables Close and Adj_Close.
+ Add returns based on Adjusted Close:
    
    - `returns`: (Adj Close / Adj Close_lag) - 1

+ Add the following range: 

    - `hi_lo_range`: this is the day's High minus Low.

+ Assign the result to `dd_feat`.

(4 pt)

In [20]:
dd_px = dd.read_parquet(PRICE_DATA).set_index("ticker") # Loading parquet files
_logs.info("Columns in dask dataframe : \n %s" , dd_px.columns) # Logging columns of dataframe

# Transformation
dd_feature = (dd_px.groupby('ticker', group_keys=False).apply(
    lambda x: x.assign(Close_lag_1 = x['Close'].shift(1))
).assign(
    returns = lambda x: x['Close']/x['Close_lag_1'] - 1
).assign(
    positive_return = lambda x: (x['returns'] > 0)*1
).assign(
    hi_lo_range = lambda x: x['High'] - x['Low']
))
_logs.info("\n\n After Transformation: \n\n %s ",dd_feature.head(5))
_logs.info("\n\n Columns after transformation :\n %s ",dd_feature.columns)


2024-10-27 19:41:48,112, 560475877.py, 2, INFO, Columns in dask dataframe : 
 Index(['Date', 'Open', 'High', 'Low', 'Close', 'Adj Close', 'Volume', 'sector',
       'subsector', 'year'],
      dtype='object')
2024-10-27 19:41:48,112, 560475877.py, 2, INFO, Columns in dask dataframe : 
 Index(['Date', 'Open', 'High', 'Low', 'Close', 'Adj Close', 'Volume', 'sector',
       'subsector', 'year'],
      dtype='object')
INFO:__main__:Columns in dask dataframe : 
 Index(['Date', 'Open', 'High', 'Low', 'Close', 'Adj Close', 'Volume', 'sector',
       'subsector', 'year'],
      dtype='object')
2024-10-27 19:44:11,823, 560475877.py, 14, INFO, 

 After Transformation: 

              Date   Open   High    Low  Close  Adj Close   Volume  \
ticker                                                              
HUM    2003-01-02  10.10  10.35  10.03  10.31   9.205751   856400   
HUM    2003-01-03  10.32  10.48  10.31  10.40   9.286115   795300   
HUM    2003-01-06  10.48  10.50  10.26  10.32   9.2146

+ Convert the Dask data frame to a pandas data frame. 
+ Add a rolling average return calculation with a window of 10 days.
+ *Tip*: Consider using `.rolling(10).mean()`.

(3 pt)

In [8]:
# Write your code below.




Please comment:

+ Was it necessary to convert to pandas to calculate the moving average return?
+ Would it have been better to do it in Dask? Why?

(1 pt)

## Criteria

The [rubric](./assignment_1_rubric_clean.xlsx) contains the criteria for grading.

## Submission Information

🚨 **Please review our [Assignment Submission Guide](https://github.com/UofT-DSI/onboarding/blob/main/onboarding_documents/submissions.md)** 🚨 for detailed instructions on how to format, branch, and submit your work. Following these guidelines is crucial for your submissions to be evaluated correctly.

### Submission Parameters:
* Submission Due Date: `HH:MM AM/PM - DD/MM/YYYY`
* The branch name for your repo should be: `assignment-1`
* What to submit for this assignment:
    * This Jupyter Notebook (assignment_1.ipynb) should be populated and should be the only change in your pull request.
* What the pull request link should look like for this assignment: `https://github.com/<your_github_username>/production/pull/<pr_id>`
    * Open a private window in your browser. Copy and paste the link to your pull request into the address bar. Make sure you can see your pull request properly. This helps the technical facilitator and learning support staff review your submission easily.

Checklist:
- [ ] Created a branch with the correct naming convention.
- [ ] Ensured that the repository is public.
- [ ] Reviewed the PR description guidelines and adhered to them.
- [ ] Verify that the link is accessible in a private browser window.

If you encounter any difficulties or have questions, please don't hesitate to reach out to our team via our Slack at `#cohort-3-help`. Our Technical Facilitators and Learning Support staff are here to help you navigate any challenges.